## Preliminary Steps

In [2]:
import math  # For general maths
import numpy as np  # For fast maths operations

# Import our relevant libraries here
# Try to keep them here instead of scattered all over the notebook....
import pandas as pd  # For easy data manipulations
from datetime import datetime, date  # For date and time functionality
import sqlalchemy as sa  # For database functionality

# For plotting from pandas. E.g. df.plot()
# Also useful for making histograms
# For histogram support with plotly, see: https://www.plot.ly/matplotlib/histograms/
import matplotlib.pyplot as plt
%matplotlib inline  

# import plotly files. These will help with plotting in an
# interactive way. 
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from plotly.graph_objs import Scatter, Figure, Layout, Histogram
from plotly import tools
init_notebook_mode(connected=True)

In [63]:
# Some nice defaults for plotting in plotly
def plot(data, title='', show_legend=True, hover_info = True, zoom=True, interactive=True):
    if not interactive:
        hover_info = False
        zoom = False
        
    if not hover_info:
        for d in data:
            try:
                d.hoverinfo='skip'
            except:
                pass
    
    layout = Layout(title=title, legend=dict(orientation="h"))
    layout.xaxis.fixedrange = not zoom
    layout.yaxis.fixedrange = not zoom
    fig = Figure(data=data, layout=layout)
    config=dict(displayModeBar=False)
    iplot(fig, show_link=False, config=config)
    
def plot_subplot(data, titles, main_title, rows, cols, show_legend=True, 
                 hover_info=True, zoom=True, interactive=True):
    # Plot subplots. Order of plots are along each row one at a time. 
    # For example: 
    #     1 2 3 4
    #     5 6 7 8
    # According to source code we can make figure last
    # https://github.com/plotly/plotly.py/blob/master/plotly/tools.py
    assert rows*cols == len(data)
    
    if not interactive:
        hover_info = False
        zoom = False
    
    fig = tools.make_subplots(rows=rows, cols=cols, subplot_titles=titles)
    for i, d in enumerate(data):
        n = i+1
        d.xaxis = 'x{}'.format(n)
        d.yaxis = 'y{}'.format(n)
        fig['layout']['xaxis{}'.format(n)].update(fixedrange=not zoom)
        fig['layout']['yaxis{}'.format(n)].update(fixedrange=not zoom)
        if not hover_info:
            d.hoverinfo='skip'

    fig['data'] = data
    fig['layout'].update(showlegend=show_legend, 
                         title=main_title, 
                         legend=dict(orientation="h"))
    config=dict(displayModeBar=False)
    iplot(fig, show_link=False, config=config)    

In [3]:
# Create a database file using sqlite
engine = sa.create_engine('sqlite:///cl_basic_data_analysis.db')
# Make it easier to download data by making a generatic function
def data_from_table(table_name, index_col=None):
    return pd.read_sql_query('SELECT * FROM {}'.format(table_name), 
                             con=engine, index_col=index_col)

## Running our data analysis 

Now the goal is to run as many different types of analysis as possible. We can measure many things from here using the columns provided. 

In [4]:
# Grab our data again. 
df_query = data_from_table('cl_data', 'index')
df_query.head()

open   high    low  close  volume  openint contract_name  year  month  \
index                                                                           
0      29.01  29.56  29.01  29.40     949      470     CL1983-06  1983      3   
1      29.40  29.60  29.25  29.29     521      523     CL1983-06  1983      3   
2      29.30  29.70  29.29  29.44     156      583     CL1983-06  1983      4   
3      29.50  29.80  29.50  29.71     175      623     CL1983-06  1983      4   
4      29.90  29.92  29.65  29.90     392      640     CL1983-06  1983      4   

       day contract_symbol  contract_year  contract_month  
index                                                      
0       30              CL           1983               6  
1       31              CL           1983               6  
2        4              CL           1983               6  
3        5              CL           1983               6  
4        6              CL           1983               6

In [5]:
# We will probably want to use a datetime field for plotting so we will do that now
def gen_datetime_col(df, year_col, month_col, day_col):
    # Takes in 3 series: year, month and day, and converts to a new series of type date
    return df[[year_col, month_col, day_col]].apply(lambda x: date(x[0], x[1], x[2]), axis=1)
        

df_query['datetime'] = gen_datetime_col(df_query, 'year', 'month', 'day')

In [6]:
# Group by year to see trends of prices
valued_columns = ['open', 'high', 'low', 'close', 'volume', 
                  'openint']
price_columns = ['open', 'high', 'low', 'close']

# Group by year and take the mean to create each row
yearly_grouping = df_query[valued_columns + ['year']].groupby('year')
yearly_mean_data = yearly_grouping.mean()
yearly_mean_data.head()

open       high        low      close       volume       openint
year                                                                       
1983  30.216106  30.292112  30.134009  30.205582   232.043822   1192.375718
1984  29.065029  29.121775  28.998625  29.056379   602.599869   2514.413556
1985  26.185423  26.283951  26.101055  26.199217  1173.599882   4256.212766
1986  15.010386  15.210992  14.778418  14.968677  3012.422166   9015.106817
1987  18.648860  18.742027  18.544287  18.638669  5556.424092  16075.234799

In [7]:
# We will also be interested in the standard deviation during each year
# We can do this by grouping by year and taking standard deviation instead of mean
yearly_std_data = yearly_grouping.std()
yearly_std_data.head()

open      high       low     close       volume       openint
year                                                                   
1983  1.073884  1.065167  1.090595  1.083780   436.073840   1679.801766
1984  1.339151  1.341686  1.330567  1.330188  1228.164653   3987.987326
1985  1.301753  1.325256  1.296856  1.321382  2360.247963   7012.812875
1986  2.689173  2.675528  2.662797  2.659623  5416.378599  11967.490558
1987  1.197400  1.195176  1.208783  1.204411  9661.649823  20057.738917

In [31]:
# Plot the data by grouping years
mdf = yearly_mean_data[['open']]
sdf = yearly_std_data[['open']]

data=[Scatter(x=mdf.index, y=mdf['open'], name='Mean Open prices per year'),
      Scatter(x=sdf.index, y=sdf['open'], name='Standard Deviation per year')]
plot(data, 'Open Price Averages Grouped By Years', interactive=False)

The charts above show a huge spike in oil contract prices from 2003 to 2008. In 2009 there was a sharp decline, following by a two year increase. After 2011, prices have rapidly fallen until 2016. Since 2003 the normal trends for the futures have vanished and replaced by a relatively rapidly changing market. 

#### Standard deviation, deviation in general

Standard deviation will normally play a huge role in how to interpret the volatility of the data. A large standard deviation indicates a large spread, and from the data the standard deviaton remained fairly consistent until 2008, where it skyrocketed. 

Indeed in 2008 news outlets (e.g. https://www.cbsnews.com/news/us-gasoline-prices-skyrocket/) talked about huge increases in the price of gas. 

Unfortunately we **don't know if the data is normally distributed**. Instead, we can measure the volatility in other ways, such as difference between High and Low prices. This should be approximately the same shape as the standard deviation.

In [33]:
df_diff = df_query['high'] - df_query['low']
df_diff.name = 'diff'
df_with_diff = pd.concat((df_query, df_diff), axis=1)
g = df_with_diff.groupby('year')
mdf = g.mean()
sdf = g.std()
plot([Scatter(x=mdf.index, y=mdf['diff'], name='High - Low prices averaged over a year'),
      Scatter(x=sdf.index, y=sdf['open']/10, name='Std Dev of Open Prices div 10')],
     title='Shapes of graphs of Difference of prices and Standard Deviation')

#### But is the data normally distributed?

Obviously the price of gas hiked significant amounts in 2008, and this event was potentially unexpected. If we want to fit a model that predicts the prices we need to make sure the volatility measurement was accurate. 

In [62]:
years = list(range(1998, 2010))
titles = ['Year {} data'.format(year) for year in years]
data = []

for year in years:
    open_data_year = df_query[df_query['year'] == year]['open'].tolist()
    trace = Histogram(x=open_data_year, opacity=0.8, histnorm='probability', nbinsx=50, name=str(year))
    data.append(trace)
    
title='Distribution of opening Crude Oil Futures prices over 12 years'
plot_subplot(data, titles=titles,  main_title=title, rows=3, cols=4, show_legend=False, interactive=False)

This is the format of your plot grid:
[ (1,1) x1,y1 ]    [ (1,2) x2,y2 ]    [ (1,3) x3,y3 ]    [ (1,4) x4,y4 ]  
[ (2,1) x5,y5 ]    [ (2,2) x6,y6 ]    [ (2,3) x7,y7 ]    [ (2,4) x8,y8 ]  
[ (3,1) x9,y9 ]    [ (3,2) x10,y10 ]  [ (3,3) x11,y11 ]  [ (3,4) x12,y12 ]



But what happens when we group by datetime and take the average of all the contracts in a single day? 

In [64]:
years = list(range(1998, 2010))
titles = ['Year {} data'.format(year) for year in years]
data = []

for year in years:
    open_data_year = df_query[df_query['year'] == year].groupby('datetime').mean()['open'].tolist()
    trace = Histogram(x=open_data_year, opacity=0.8, histnorm='probability', nbinsx=50, name=str(year))
    data.append(trace)
    
title='Distribution of opening Crude Oil Futures prices over 12 years'
plot_subplot(data, titles=titles,  main_title=title, rows=3, cols=4, show_legend=False, interactive=False)

This is the format of your plot grid:
[ (1,1) x1,y1 ]    [ (1,2) x2,y2 ]    [ (1,3) x3,y3 ]    [ (1,4) x4,y4 ]  
[ (2,1) x5,y5 ]    [ (2,2) x6,y6 ]    [ (2,3) x7,y7 ]    [ (2,4) x8,y8 ]  
[ (3,1) x9,y9 ]    [ (3,2) x10,y10 ]  [ (3,3) x11,y11 ]  [ (3,4) x12,y12 ]



In the first chart we can see the data gets pretty wacky in some years (eg. 2002, 2007 and 2008 do not fit our usual distributions). Furthermore there does not appear to be any direct visual correclation between standard deviation and the shape of each disribution.

The second chart shows what we have been fearin: if you take the average price of all contracts in an given day, it will not provide you with any information. This means the contracts dictate the way the data is distributed. 

## Analyzing contract by month

In [351]:
df_yearly_contract_month = df_query.groupby(('contract_year', 'contract_month')).mean().reset_index()
df = df_yearly_contract_month
x = df[['contract_year', 'contract_month']].apply(lambda x: '{}-{:02d}'.format(x[0], x[1]), axis=1)
layout = dict(title = 'Average value of contracts over its life')
fig = dict(data=[Scatter(x=x, y=df['open'], mode='markers')], layout=layout)
iplot(fig)

Woah! There are some wierd things going on here. There are two trendlines. Looking closer we can see that these are months that follow different trendlines. June and December in particular stand out:

In [354]:
df['open'].max()

92.83639892904948

In [365]:
# To Avoid stairstepping, let's plot all the contracts by month:
df_yearly_contract_month = df_query.groupby(('contract_year', 'contract_month')).mean().reset_index()
df = df_yearly_contract_month
df['contract_date'] = df[['contract_year', 'contract_month']].apply(lambda x: '{}-{:02d}'.format(x[0], x[1]), axis=1)
layout = dict(title = 'Average value of contracts over its life')

months = ['', 'Jan', 'Feb', 'Mar', 'Apr', 'May', 'Jun', 'Jul', 'Aug', 'Sep', 'Oct', 'Nov', 'Dec']
data = []
for m in range(1, 13):
    d = df[df['contract_month'] == m]
    data.append(Scatter(x=d['contract_date'], y=d['open'], name='{} Contract'.format(months[m])))
    
fig = dict(data=data, layout=layout)
iplot(fig)

As we can see the data has trends that have varied over the years, establishing new trends. 

## Adjusting contract data for volume

What happens to the life of a contract? Surely it doesn't have a constant trading size over its life. We can see that most of the contracts aren't traded on over the course of their lives:

In [421]:
df = df_with_diff
pct = df[df['diff'] == 0].shape[0]*100./df.shape[0]
print('{:.2f}% of contracts have a High - Low difference of 0 (no change)'.format(pct))

61.42% of contracts have a High - Low difference of 0 (no change)


**This is great!** We can assume that contracts that don't change in price do not have people trading on them. Not only that but the volume will be close to 0 for these contracts. Let's look at a single contract:

In [441]:
df = df_query[df_query['contract_name'] == 'CL2001-01']
iplot([Scatter(x=df['datetime'], y=df['volume'], mode='markers')])

The trend is exponential! How do we choose when the cutoff is for the volumes we care about? For now I will try a way to make a good selection. Let's compare the contract to the market:

In [476]:
df = df_query[df_query['contract_name'] == 'CL2001-01']

# Only grab data that shares the same date and time as our contract above
df_iso = df_query.merge(df[['datetime']], how='right', on='datetime')
df_iso = df_iso.groupby('datetime').mean()
iplot([Scatter(x=df['datetime'], y=df['open'], name='CL2001-01 open prices'),
       Scatter(x=df_iso.index, y=df_iso['open'], name='Average open prices in market')])

We see an obvious deviation in January of the year 2000. I strongly suspect this is because of low-volume contracts influencing the market, so let's remove all contracts that are not within a year of their expiration:

In [482]:
df = df_query[df_query['contract_name'] == 'CL2001-01']

# Only grab data that shares the same date and time as our contract above
df_iso = df_query.merge(df[['datetime']], how='right', on='datetime')

# Separate out the contracts that expire more than a year after any given date
# This logic is in parts: if the year difference is less than one, the contracts are definitely 
# within a year of each other. If the difference is exactly one, then the contracts
# are within a year of each other if the contracts month is less than the date's month
# This assume (correctly) the that the contract expire by the time they hit date
year_diff = df_iso['contract_year'] - df_iso['year']
df_bool = (year_diff < 1) | (year_diff == 1) & (df_iso['contract_month'] <= df_iso['month'])
df_iso = df_iso[df_bool]


df_iso = df_iso.groupby('datetime').median()
iplot([Scatter(x=df['datetime'], y=df['open'], name='CL2001-01 open prices'),
       Scatter(x=df_iso.index, y=df_iso['open'], name='Average open prices in market')])

The trend no longer follows. What if we cut off the contracts when 1% of the total volume has been filled?

In [535]:
df = df_query[df_query['contract_name'] == 'CL2001-01']
total_volume = df['volume'].sum()
cum_volume = df['volume'].cumsum()
cum_pcts = cum_volume*100./total_volume

# Get the dates where cumulative percents are met at the following intervals
x, y, text = [], [], []
for p in [1, 5, 10, 20, 50, 100]:
    d = df[cum_pcts < p].tail(1)
    x.append(d['datetime'].tolist()[0])
    y.append(cum_volume[d.index].tolist()[0])
    text.append('{}%'.format(p))
    

iplot([Scatter(x=df['datetime'], y=cum_volume, name='Cumulative Volume of CL2001-01'),
       Scatter(x=x, y=y, mode='markers+text', text=text, name='Percentage of total volume')])

[datetime.date(1999, 10, 15), datetime.date(2000, 5, 19), datetime.date(2000, 9, 6), datetime.date(2000, 10, 11), datetime.date(2000, 11, 16), datetime.date(2000, 12, 18)] [29468, 148934, 296782, 564215, 1485200, 2939644]
